## CS166: Elevator Simulation
Group members: Galena, Urmila, Long, Valyo, Qiqi 


In [42]:
import random
import numpy as np

class Elevator():

    """ Models an elevator 
    Attributes:
        current_floor = An integer representing the elevator's current floor
        num_floors = An integer representing the number of floors the elevator can travel
        action_queue = A list representing passengers that need to be delivered to their destination
        max_capacity = An integer indicating how many passengers can fit in the elevator 
        passengers_inside = A list of passenger objects whose pickedup attribute == True. That is, a list of passengers inside the elvator. """

    def __init__(self, num_floors, current_floor = 1, direction="up", max_capacity = 300): #user must manually update max_capacity to change the elevator capacity.

        self.current_floor = current_floor
        self.num_floors = num_floors
        self.action_queue = []  # next floor to stop at
        self.max_capacity = max_capacity 
        self.passengers_inside = [] # list of passengers inside the elevator

    def add_request(self, passenger):

        """ Add passengers to the action queue if capacity allows """
        if len(self.passengers_inside) <= self.max_capacity :
            self.passengers_inside.append(passenger)  
            self.action_queue.append(passenger.destination)
            passenger.pickedup = True

    def completed(self, passenger, sim_time):

        """ Remove passengers who have been delivered to their destination """

        self.passengers_inside.remove(passenger)
        self.action_queue.remove(passenger.destination)
        passenger.pickedup = False
        passenger.reached = True
        passenger.delivery_time = sim_time
        print "Next Actions:",self.action_queue
        
    def move(self, curr_fl):
        self.current_floor = curr_fl

class Passenger():

    """ Models a passenger
    Attributes:
        starting_floor = An integer representing the floor the passenger starts on 
        destination = An integer representing the floor the passenger is going to 
        pickedup.reached= Both Boolean values indicating whether a paasenger is picked up / has reached destination """

    def __init__(self, num_floors, pickedup=False, reached=False):
        self.starting_floor = random.randint(1, num_floors)
        self.destination = random.choice([i for i in range(1,num_floors+1) if i!=self.starting_floor])
        self.pickedup = pickedup #default: False
        self.reached = reached #default: False
        self.direction = "up" if self.destination > self.starting_floor else "down"
        self.delivery_time = 0

class Building():

    """ Models a building
    Attributes:
        num_floors = An integer representing the number of floors in the building
        num_passengers = An integer indicating how many passengers there are in the building
        """
    

    def __init__(self, num_passengers, num_floors=10):

        self.num_floors = num_floors
        self.num_passengers = num_passengers
        self.passengers_remained = num_passengers
        self.simulation_time = 0

    def execution_simple(self):
        """ Implement the naive execution strategy:
        The Elevator stops at every floor, picking up passengers, if any, regardless of their intended direction,
        until all passengers have arrived at their respective destination"""
        elevator = Elevator(self.num_floors)

        pass_list = []
        #to store inidividual passenger wait times
        deliverytime_list = []
        self.passenger_delivery_times=[]
        
        for x in range(self.num_passengers):
            y = Passenger(self.num_floors)
            pass_list.append(y)
        
        while self.passengers_remained > 0: #start loop, the elevator would keep going all the way up and all the way down until no passengers are left
            for fl in range(0, self.num_floors):

                elevator.move(fl+1) #move 1 floor and door opens, 12 seconds
                self.simulation_time += 12
                
                for passenger in pass_list:

                    if elevator.current_floor == passenger.starting_floor and passenger.reached==False and passenger.pickedup==False:

                        elevator.add_request(passenger) 
                        self.simulation_time += 10

                    if elevator.current_floor == passenger.destination and passenger.reached==False and passenger.pickedup==True:
                        elevator.completed(passenger, self.simulation_time)
                        self.passengers_remained -= 1
                        deliverytime_list.append(self.simulation_time)
                        print "Total number of remaining passengers:",(self.passengers_remained)
                        if self.passengers_remained == 0:                        
                            self.passenger_delivery_times=deliverytime_list
                            print "Simulation Complete; no passengers remaining"
                            print "Total time take:", self.simulation_time
                            return 


            for fl in range(self.num_floors+1, 1, -1):
                
                elevator.move(fl-1) #move 1 floor and door opens, 12 seconds
                self.simulation_time += 12
                
                for passenger in pass_list:

                    if elevator.current_floor == passenger.starting_floor and passenger.reached==False and passenger.pickedup==False:
                        elevator.add_request(passenger) 
                        
                    if elevator.current_floor == passenger.destination and passenger.reached==False and passenger.pickedup==True:
                        elevator.completed(passenger, self.simulation_time) 
                        self.passengers_remained -= 1
                        deliverytime_list.append(self.simulation_time)

                        print "Total number of remaining passengers:", self.passengers_remained
                        if self.passengers_remained == 0:
                            self.passenger_delivery_times=deliverytime_list
                            print "Simulation Complete; no passengers remaining"
                            print "Total time take:",self.simulation_time
                            return
                        

                    
    def execution(self):
        """ Implement the improved strategy
        The elevator only picks up passengers that are going in the same direction as it is moving towards. 
        The iteration ends when all passengers have arrived at their respective destination"""
        #initiate pass list
        elevator = Elevator(self.num_floors)

        pass_list = []
        #to store inidividual passenger wait times
        deliverytime_list = []
        self.passenger_delivery_times=[]
        
        for x in range(self.num_passengers):
            y = Passenger(self.num_floors)
            pass_list.append(y)
            
        while self.passengers_remained > 0: #start loop, the elevator would keep going all the way up and all the way down until no passengers are left
            for fl in range(0, self.num_floors):
                door_open = False
                elevator.move(fl+1) #move floors, 2 seconds
                self.simulation_time += 2
                
                for passenger in pass_list:
                    
                    if elevator.current_floor == passenger.starting_floor and passenger.reached==False and passenger.pickedup==False and passenger.direction=="up":
                        elevator.add_request(passenger)
                        door_open = True

                    if elevator.current_floor == passenger.destination and passenger.reached==False and passenger.pickedup==True:
                        elevator.completed(passenger, self.simulation_time)
                        self.passengers_remained -= 1
                        deliverytime_list.append(self.simulation_time)
                        
                        print "Total number of remaining passengers:", self.passengers_remained
                        door_open = True
                        
                    if self.passengers_remained == 0:
                        self.passenger_delivery_times=deliverytime_list
                        self.simulation_time =+ 10 #add 10 secs for door opening
                        print "Simulation Complete; no passengers remaining"
                        
                        print "Total time taken:", self.simulation_time
                        return
                if door_open: #door opens, add 10 seconds
                        self.simulation_time += 10

            for fl in range(self.num_floors+1, 1, -1):
                elevator.move(fl-1) #move floors, 2 seconds
                self.simulation_time += 2
                
                for passenger in pass_list:
                    door_open = False
                    
                    if elevator.current_floor == passenger.starting_floor and passenger.reached==False and passenger.pickedup==False and passenger.direction == "down":

                        elevator.add_request(passenger)
                        door_open = True

                    if elevator.current_floor == passenger.destination and passenger.reached==False and passenger.pickedup==True:
                        elevator.completed(passenger, self.simulation_time)               
                        self.passengers_remained -= 1
                        deliverytime_list.append(self.simulation_time)
                        
                        print "Total number of remaining passengers:", self.passengers_remained
                        door_open = True
                    if door_open :
                        self.simulation_time += 10
                    
                    if self.passengers_remained == 0:                            
                        self.passenger_delivery_times=deliverytime_list
                        print "Simulation Complete; no passengers remaining"
                        print "Total time taken:", self.simulation_time
                        return

In [16]:
#sanity check, one iteration
build_simple = Building(20)
build_simple.execution_simple()

Next Actions: [6, 9, 10]
Total number of remaining passengers: 19
Next Actions: [9, 10, 3]
Total number of remaining passengers: 18
Next Actions: [10, 3, 5]
Total number of remaining passengers: 17
Next Actions: [3, 5, 6]
Total number of remaining passengers: 16
Next Actions: [3, 5, 1]
Total number of remaining passengers: 15
Next Actions: [3, 1]
Total number of remaining passengers: 14
Next Actions: [1, 10, 9]
Total number of remaining passengers: 13
Next Actions: [10, 9, 8]
Total number of remaining passengers: 12
Next Actions: [10, 9, 8]
Total number of remaining passengers: 11
Next Actions: [10, 9, 10]
Total number of remaining passengers: 10
Next Actions: [10, 10, 3]
Total number of remaining passengers: 9
Next Actions: [10, 3, 3]
Total number of remaining passengers: 8
Next Actions: [3, 3]
Total number of remaining passengers: 7
Next Actions: [3, 3, 10]
Total number of remaining passengers: 6
Next Actions: [3, 10]
Total number of remaining passengers: 5
Next Actions: [10]
Total n

In [17]:
#sanity check: 1 iteration
import numpy as np
simple_wait_times = build_simple.passenger_delivery_times
simple_mean = np.mean(simple_wait_times)
simple_max = np.max(simple_wait_times)
print "average wait time:",simple_mean
print "maximum wait time:",simple_max

average wait time: 586.0
maximum wait time: 1028


In [18]:
#sanity check: 1 iteration
build_improved = Building(20)
build_improved.execution()

Next Actions: [9, 10, 10]
Total number of remaining passengers: 19
Next Actions: [10, 10, 10]
Total number of remaining passengers: 18
Next Actions: [10, 10]
Total number of remaining passengers: 17
Next Actions: [10]
Total number of remaining passengers: 16
Next Actions: []
Total number of remaining passengers: 15
Next Actions: [2, 2, 8]
Total number of remaining passengers: 14
Next Actions: [2, 2]
Total number of remaining passengers: 13
Next Actions: [2, 2, 2]
Total number of remaining passengers: 12
Next Actions: [2, 2]
Total number of remaining passengers: 11
Next Actions: [2]
Total number of remaining passengers: 10
Next Actions: []
Total number of remaining passengers: 9
Next Actions: [10, 9]
Total number of remaining passengers: 8
Next Actions: [10]
Total number of remaining passengers: 7
Next Actions: []
Total number of remaining passengers: 6
Next Actions: [7, 4, 2]
Total number of remaining passengers: 5
Next Actions: [4, 2]
Total number of remaining passengers: 4
Next Actio

In [20]:
#sanity check: 1 iteration
improved_wait_times = build_improved.passenger_delivery_times
improved_mean = np.mean(improved_wait_times)
improved_max = np.max(improved_wait_times)
print "average wait time:",improved_mean
print "maximum wait time:",improved_max

average wait time: 274.4
maximum wait time: 490


In [44]:
%%capture
#simulation: 1000 iterations
simple_wait_times_mean = []
simple_wait_times_max = []
for i in range(1000):
    build_simple = Building(20)
    build_simple.execution_simple()
    simple_wait_times_mean.append(np.mean(build_simple.passenger_delivery_times))
    simple_wait_times_max.append(np.max(build_simple.passenger_delivery_times))

In [45]:
%%capture
#simulation: 1000 iterations
improved_wait_times_mean = []
improved_wait_times_max = []
for i in range(1000):
    build_improved = Building(20)
    build_improved.execution()
    improved_wait_times_mean.append(np.mean(build_improved.passenger_delivery_times))
    improved_wait_times_max.append(np.max(build_improved.passenger_delivery_times))

In [46]:
#result print-out: case 1: no cap limit
print("Average wait time, naive strat, no cap limit, after 1000 realizations: ", round(np.mean(simple_wait_times_mean), 2))
print("Max wait time, naive strat, no cap limit, after 1000 realizations: ", round(np.max(simple_wait_times_max),2))
print("Average wait time, improved strat, no cap limit, after 1000 realizations: ", round(np.mean(improved_wait_times_mean),2))
print("Max wait time, improved strat, no cap limit, after 1000 realizations: ", round(np.max(improved_wait_times_max),2))

('Average wait time, naive strat, no cap limit, after 1000 realizations: ', 317.85)
('Max wait time, naive strat, no cap limit, after 1000 realizations: ', 440.0)
('Average wait time, improved strat, no cap limit, after 1000 realizations: ', 165.94)
('Max wait time, improved strat, no cap limit, after 1000 realizations: ', 420.0)


In [41]:
#result print-out: case 2: with cap limit
print("Average wait time, naive strat, with cap limit, after 1000 realizations: ", round(np.mean(simple_wait_times_mean),2))
print("Max wait time, naive strat, with cap limit, after 1000 realizations: ", round(np.max(simple_wait_times_max),2))
print("Average wait time, improved strat, with cap limit, after 1000 realizations: ", round(np.mean(improved_wait_times_mean),2))
print("Max wait time, improved strat, with cap limit, after 1000 realizations: ", round(np.max(improved_wait_times_max),2))

('Average wait time, naive strat, with cap limit, after 1000 realizations: ', 522.36)
('Max wait time, naive strat, with cap limit, after 1000 realizations: ', 1440.0)
('Average wait time, improved strat, with cap limit, after 1000 realizations: ', 229.89)
('Max wait time, improved strat, with cap limit, after 1000 realizations: ', 716.0)
